<a href="https://colab.research.google.com/github/RaziehSh1987/3D-landmarks-Pose_estimation/blob/main/BlazePose3D_Using_2D_Keypoints_all.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

To generate the 2D keypoints, I'll provide an example using Detectron2. First, you need to install Detectron2 and its dependencies:

Install Detectron2:

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
# BlazePose3D_Using_2D_Keypoints
import torch

if torch.cuda.is_available():
    print("GPU is being used.")
else:
    print("CPU is being used.")


print(torch.__version__, torch.cuda.is_available())


GPU is being used.
2.0.0+cu118 True


In [ ]:
# check CUDA version
!nvcc --version


nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2022 NVIDIA Corporation
Built on Wed_Sep_21_10:33:58_PDT_2022
Cuda compilation tools, release 11.8, V11.8.89
Build cuda_11.8.r11.8/compiler.31833905_0


* Cython is a programming language that is a superset of Python and allows for writing Python code that can be compiled to C or C++ for improved performance. It is used for speeding up Python code by making it run at C-like speeds while still retaining the ease-of-use and dynamic nature of Python.

* 'git+https://github.com/cocodataset/cocoapi.git#subdirectory=PythonAPI' is a command that installs the COCO API package for Python using pip.

COCO (Common Objects in Context) is a large-scale object detection, segmentation, and captioning dataset. The COCO API provides a Python interface for accessing the dataset and working with its annotations, as well as tools for evaluating object detection and segmentation models on the dataset.

In [ ]:
# !pip install --upgrade pycocotools


In [ ]:

!pip install -U torch torchvision -f https://download.pytorch.org/whl/cu118/torch_stable.html #i changed c111 to c118
!pip install -U cython
!pip install 'git+https://github.com/cocodataset/cocoapi.git#subdirectory=PythonAPI'
!pip install -U 'git+https://github.com/facebookresearch/detectron2.git@v0.6'






Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in links: https://download.pytorch.org/whl/cu118/torch_stable.html
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.3/2.3 GB 751.6 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.1/6.1 MB 52.6 MB/s eta 0:00:00
  Attempting uninstall: torch
    Found existing installation: torch 2.0.0+cu118
    Uninstalling torch-2.0.0+cu118:
      Successfully uninstalled torch-2.0.0+cu118
  Attempting uninstall: torchvision
    Found existing installation: torchvision 0.15.1+cu118
    Uninstalling torchvision-0.15.1+cu118:
      Successfully uninstalled torchvision-0.15.1+cu118
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
torchaudio 2.0.1+cu118 requires torch==2.0.0, but you have torch 2.0.1+cu118 which is incompatible.
torchdata 0.6.0 requires torch==2

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://github.com/cocodataset/cocoapi.git to /tmp/pip-req-build-krc5s5am
  Running command git clone --filter=blob:none --quiet https://github.com/cocodataset/cocoapi.git /tmp/pip-req-build-krc5s5am
  Resolved https://github.com/cocodataset/cocoapi.git to commit 8c9bcc3cf640524c4c20a9c40e89cb6a2f2fa0e9
  Preparing metadata (setup.py) ... done
  Created wheel for pycocotools: filename=pycocotools-2.0-cp310-cp310-linux_x86_64.whl size=386209 sha256=a1eb49895db4be866e525e2ddc181d772388bbd28a601279f7482ae11a5e4462
  Stored in directory: /tmp/pip-ephem-wheel-cache-6bzwsbek/wheels/39/61/b4/480fbddb4d3d6bc34083e7397bc6f5d1381f79acc68e9f3511
Successfully built pycocotools
  Attempting uninstall: pycocotools
    Found existing installation: pycocotools 2.0.6
    Uninstalling pycocotools-2.

* Detectron is an open-source deep learning framework for object detection and segmentation tasks developed by Facebook AI Research (FAIR). It is built on top of the PyTorch deep learning framework and provides a flexible and modular implementation of state-of-the-art object detection algorithms.

Detectron supports a wide range of object detection and segmentation models, including Faster R-CNN, Mask R-CNN, RetinaNet, and DensePose. It also provides pre-trained models for various tasks, such as instance segmentation, keypoint detection, and panoptic segmentation.

Detectron has become a popular tool in the computer vision research community and has been used in a variety of applications, including autonomous driving, robotics, and medical imaging.

* setup_logger() is a function that initializes the logging system used by Detectron2. It sets the logging level, format, and destination of the log messages, and returns a logger object that can be used to log messages throughout the code.
In the context of logging, the logging level refers to the severity of the messages that are logged. There are several logging levels available, including DEBUG, INFO, WARNING, ERROR, and CRITICAL, each indicating a different level of severity.

Setting the logging level to INFO means that all log messages of severity INFO and higher (WARNING, ERROR, and CRITICAL) will be logged, while messages of lower severity (DEBUG) will be ignored.

In other words, setting the logging level to INFO will result in a moderate amount of log messages being generated, providing useful information about the program's execution without overwhelming the user with too much detail.

In [ ]:
import detectron2
from detectron2.utils.logger import setup_logger
setup_logger()


<Logger detectron2 (DEBUG)>

In [ ]:

# ## Restart the Colab runtime:
# import os
# os.kill(os.getpid(), 9)




Extract the frames from the video:

In [ ]:
# %cd ..

!rm -r frames
# %pwd

rm: cannot remove 'frames': No such file or directory


In [ ]:
import cv2
import os

# video_path = "/content/drive/MyDrive/BishopThesisv9-Medapipe-unity/input/004.mp4" # for each camera by special distance
video_path ="/content/drive/MyDrive/BishopThesisv10-3dLandmark-unity/unity/new_video_all_distances_angles/1234.mp4" # for one camera by all distances and all angles
frames_directory = "frames"

if not os.path.exists(frames_directory):
    os.makedirs(frames_directory)

cap = cv2.VideoCapture(video_path)
frame_idx = 0

while cap.isOpened():
    ret, frame = cap.read()
    
    if not ret:
        break

    frame_path = os.path.join(frames_directory, f"frame{frame_idx:04d}.png") #define a path+name for each frame
    cv2.imwrite(frame_path, frame)  #save extraceted inage into frame
    frame_idx += 1

cap.release()

**Generate the 2D keypoints using Detectron2 and save them as a .npy file:
*** After completing these steps, you'll have the 2D keypoints saved in a .npy file named "keypoints.npy". You can then proceed to run the VideoPose3D model and predict the 3D landmarks.

In [ ]:
import numpy as np
from detectron2 import model_zoo
from detectron2.engine import DefaultPredictor
from detectron2.config import get_cfg

cfg = get_cfg()
cfg.merge_from_file(model_zoo.get_config_file("COCO-Keypoints/keypoint_rcnn_R_50_FPN_3x.yaml"))
cfg.MODEL.ROI_HEADS.SCORE_THRESH_TEST = 0.7
cfg.MODEL.WEIGHTS = model_zoo.get_checkpoint_url("COCO-Keypoints/keypoint_rcnn_R_50_FPN_3x.yaml")
predictor = DefaultPredictor(cfg)

frames = sorted(os.listdir(frames_directory))

keypoints_list = []

for frame_name in frames:
    frame_path = os.path.join(frames_directory, frame_name)
    im = cv2.imread(frame_path)
    outputs = predictor(im)

    if len(outputs["instances"]) > 0:
        keypoints = outputs["instances"].to("cpu").get_fields()["pred_keypoints"][0].numpy()
        keypoints_list.append(keypoints[:, :2])
    else:
        keypoints_list.append([])

np.save("/content/drive/MyDrive/BishopThesisv10-3dLandmark-unity/BlazePose_input_output/2D_Output/keypoints1234.npy", keypoints_list) #after plot uncomment

model_final_a6e10b.pkl: 237MB [00:01, 123MB/s]                           
/usr/local/lib/python3.10/dist-packages/torch/functional.py:504: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at ../aten/src/ATen/native/TensorShape.cpp:3483.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]
/usr/local/lib/python3.10/dist-packages/numpy/lib/npyio.py:518: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  arr = np.asanyarray(arr)


----------------------------Create 3D Landmarks_Blaze_Poze----------------------------------


```
Here's a high-level overview of the steps:

Install MediaPipe and other dependencies required for running BlazePose on Google Colab.

Load the 2D keypoints for each of the four videos. we used of Detectron2 to read the video frames and extract the 2D keypoints using BlazePose.

Apply BlazePose to the 2D keypoints to obtain the 3D landmarks. You can use the pre-trained BlazePose model provided by Google, or train your own model if required.

Save the 3D landmarks for each frame of each video as a separate text file in the specified format.
```



In [ ]:
!pip install mediapipe


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 33.9/33.9 MB 16.8 MB/s eta 0:00:00


In [ ]:
import numpy as np
import matplotlib.pyplot as plt

# Load the keypoints from the saved file
keypoints_2d = np.load("/content/drive/MyDrive/BishopThesisv10-3dLandmark-unity/BlazePose_input_output/2D_Output/keypoints1234.npy", allow_pickle=True)
print(keypoints_2d)
print(keypoints_2d.shape,keypoints_2d[0].shape)


[array([[747.0674  ,  52.845543],
        [747.7379  ,  49.49821 ],
        [743.04346 ,  48.828743],
        [746.39667 ,  53.51501 ],
        [727.61847 ,  53.51501 ],
        [744.38477 ,  84.31046 ],
        [714.8762  ,  80.963135],
        [736.3369  , 111.08913 ],
        [706.8284  , 110.41966 ],
        [739.01953 , 131.84259 ],
        [709.51105 , 138.53725 ],
        [735.6663  , 137.86778 ],
        [718.9     , 135.18993 ],
        [746.39667 , 178.03577 ],
        [716.21747 , 180.04417 ],
        [734.325   , 222.89003 ],
        [706.1578  , 223.55948 ]], dtype=float32)
 array([[873.74115 ,  12.592256],
        [874.4102  ,   9.240998],
        [869.727   ,   9.240998],
        [853.0014  ,  12.592256],
        [853.0014  ,  12.592256],
        [867.7199  ,  44.09407 ],
        [842.29706 ,  36.721302],
        [855.67755 ,  72.24463 ],
        [830.25464 ,  66.212364],
        [836.9448  ,  89.00091 ],
        [834.9378  ,  91.011665],
        [854.3395  ,  91.681915]

# **below cell code works for each camera but for all distance doesnt work:**

In [ ]:
# import os
# import cv2
# import numpy as np
# import mediapipe as mp
# frame_idx=0
# # Load the 2D keypoints from the saved file
# keypoints_2d = np.load("/content/drive/MyDrive/BishopThesisv10-3dLandmark-unity/BlazePose_input_output/2D_Output/keypoints1234.npy")#i've added ", allow_pickle=True" 

# # Create a MediaPipe BlazePose model
# mp_drawing = mp.solutions.drawing_utils
# mp_pose = mp.solutions.pose

# with mp_pose.Pose(
#     min_detection_confidence=0.5,
#     min_tracking_confidence=0.5) as pose_model:

#     # Initialize an empty list to store the 3D landmarks
#     landmarks_3d = []

#     max_num_keypoints = 17

#     # Loop through each frame of the video
#     for keypoints in keypoints_2d:
#       # print(keypoints)#[[453.30832   71.24796 ]..]
#     # Extract the 3D landmarks from the 2D keypoints
#       input_keypoints = np.expand_dims(keypoints, axis=0)
#       # print(keypoints.shape,input_keypoints.shape)#(17, 2) (1, 17, 2)
#       num_keypoints = input_keypoints.shape[1] #17
     
#       # # if num_keypoints < 24:
#       # #     input_keypoints = np.pad(input_keypoints, ((0,0),(0,24-num_keypoints),(0,0)), mode='constant') # Add zeros for the missing keypoints
      
#       # # Pad the input_keypoints array with zeros to the maximum length
#       if num_keypoints < max_num_keypoints:
#           input_keypoints = np.pad(input_keypoints, ((0,0),(0,max_num_keypoints-num_keypoints),(0,0)), mode='constant') # Add zeros for the missing keypoints
#       elif num_keypoints > max_num_keypoints:
#           max_num_keypoints = num_keypoints
#           input_keypoints = np.pad(input_keypoints, ((0,0),(0,max_num_keypoints-num_keypoints),(0,0)), mode='constant') # Add zeros for the missing keypoints
            
#       input_keypoints = np.transpose(input_keypoints, (0,2,1)) # Swap the second and third axes
#       print(input_keypoints)#[0][0][:])
      
#       # try:
#       # Load the image
#       frame_name = f"frame{frame_idx:04d}.png"# "{:04d}.jpg".format(frame_idx)
#       frame_path = os.path.join(frames_directory, frame_name)
#       im = cv2.imread(frame_path)
#       # print(frame_name)#frame0056.png
#       # print(im.shape)#(466, 952, 3)

#       # Convert the image to RGB if needed
#       if im.shape[2] != 3:
#           im = cv2.cvtColor(im, cv2.COLOR_GRAY2RGB)

#       # Run the BlazePose model on the image and the 2D keypoints
#       results = pose_model.process(image=im)#, landmarks=input_keypoints[0][0][:])

#       # Extract the 3D landmarks from the results
#       landmarks = []
#       if results.pose_landmarks:
#           for landmark in results.pose_landmarks.landmark:
#               landmarks.append((landmark.x, landmark.y, landmark.z))  #0.48833927512168884 0.12189597636461258 -0.004090915899723768
            
#       else:
#           landmarks = [(-1, -1, -1)] * 33 # * num_keypoints 

#       print(np.array(landmarks))
      
#       # Add the 3D landmarks to the list
#       landmarks_3d.append(np.array(landmarks))

       
#       # except TypeError as e:
#       #   print(f"Error: {e}")

#       frame_idx += 1



# **bellow code works for all distance and angles:**

In [ ]:
import os
import cv2
import numpy as np
import mediapipe as mp
frame_idx=0

# Load the 2D keypoints from the saved file
keypoints_2d = np.load("/content/drive/MyDrive/BishopThesisv10-3dLandmark-unity/BlazePose_input_output/2D_Output/keypoints1234.npy", allow_pickle=True)#i've added ", allow_pickle=True" 

# Create a MediaPipe BlazePose model
mp_drawing = mp.solutions.drawing_utils
mp_pose = mp.solutions.pose

with mp_pose.Pose(
    min_detection_confidence=0.5,
    min_tracking_confidence=0.5) as pose_model:

    # Initialize an empty list to store the 3D landmarks
    landmarks_3d = []
# ----------------------------------------
    max_num_keypoints = 20  #17

    # Loop through each frame of the video
    for keypoints in keypoints_2d:
      # print(keypoints)#[[453.30832   71.24796 ]..]
      num_keypoints = len(keypoints)  # Number of keypoints in the list
      
       # Convert the keypoints list into a NumPy array
      keypoints_array = np.array(keypoints)
      # Extract the 3D landmarks from the 2D keypoints
      input_keypoints = np.expand_dims(keypoints, axis=0)
      # # print(keypoints.shape,input_keypoints.shape)#(17, 2) (1, 17, 2)
      # num_keypoints = input_keypoints.shape[1] #17
     
      # # if num_keypoints < 24:
      # #     input_keypoints = np.pad(input_keypoints, ((0,0),(0,24-num_keypoints),(0,0)), mode='constant') # Add zeros for the missing keypoints
      
      # # Pad the input_keypoints array with zeros to the maximum length
      if num_keypoints !=0 :     
        if num_keypoints < max_num_keypoints:
            print(num_keypoints)
            input_keypoints = np.pad(input_keypoints, ((0,0),(0,max_num_keypoints-num_keypoints),(0,0)), mode='constant') # Add zeros for the missing keypoints
        elif num_keypoints > max_num_keypoints:
            max_num_keypoints = num_keypoints
            input_keypoints = np.pad(input_keypoints, ((0,0),(0,max_num_keypoints-num_keypoints),(0,0)), mode='constant') # Add zeros for the missing keypoints
              
        input_keypoints = np.transpose(input_keypoints, (0,2,1)) # Swap the second and third axes
        print(input_keypoints)#[0][0][:])
   
        # try:
        # Load the image
        frame_name = f"frame{frame_idx:04d}.png"# "{:04d}.jpg".format(frame_idx)
        frame_path = os.path.join(frames_directory, frame_name)
        im = cv2.imread(frame_path)
        # print(frame_name)#frame0056.png
        # print(im.shape)#(466, 952, 3)

        # Convert the image to RGB if needed
        if im.shape[2] != 3:
            im = cv2.cvtColor(im, cv2.COLOR_GRAY2RGB)

        # Run the BlazePose model on the image and the 2D keypoints
        results = pose_model.process(image=im)#, landmarks=input_keypoints[0][0][:])

        # Extract the 3D landmarks from the results
        landmarks = []
        if results.pose_landmarks:
            for landmark in results.pose_landmarks.landmark:
                landmarks.append((landmark.x, landmark.y, landmark.z))  #0.48833927512168884 0.12189597636461258 -0.004090915899723768
              
        else:
            landmarks = [(-1, -1, -1)] * 33 # * num_keypoints 

        print(np.array(landmarks))
        
        # Add the 3D landmarks to the list
        landmarks_3d.append(np.array(landmarks))

        
        # except TypeError as e:
        #   print(f"Error: {e}")
        print(frame_idx)
        frame_idx += 1
      else:
        pass




Streaming output truncated to the last 5000 lines.
 [-1 -1 -1]
 [-1 -1 -1]]
550
17
[[[388.55444 389.8759  385.91156 391.85803 379.30438 395.1616  372.69724
   397.80447 370.05438 401.10803 373.35794 391.85803 380.62582 392.5187
   389.8759  390.5366  378.6437    0.        0.        0.     ]
  [178.40065 174.38872 176.39468 171.71413 176.39468 180.40662 186.42448
   196.45427 204.47813 212.50195 221.19444 209.15869 210.496   235.23616
   235.90482 261.98227 234.5675    0.        0.        0.     ]]]
[[-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]
 [-1 -1 -1]]
551
17
[[[384.3071  383.64227 378.9886  385.63672 371.67563 390.29044 366.35712
   392.28485 365.02

In [ ]:
print(len(landmarks_3d))
for i in range(0,len(landmarks_3d)):
  print(len(landmarks_3d[i]))
  if len(landmarks_3d[i])!=33:
    print(f'{landmarks_3d[i]}----------------------------')

672
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33
33


#after plot uncomment below code:

In [ ]:
# save 3d coordinates as a Text file
def save_coordinates(filename, coordinates, landmark_numbers):
    with open(filename, "w") as file:
        for i in range(len(coordinates)):
            # file.write(f"Landmark {landmark_numbers[i]}: ({coordinates[i][0]}, {coordinates[i][1]}, {coordinates[i][2]})\n")
          #  for j in range(0,len(landmark_numbers[i])-1):
           for j in range(0,len(landmark_numbers)):
            #  file.write(f"Landmark [{i},{landmark_numbers[j]}]: {coordinates[i][j]}\n")
             file.write(f"Landmark [{i},{landmark_numbers[j]}]: ({coordinates[i][j][0]}, {coordinates[i][j][1]}, {coordinates[i][j][2]})\n")


filename = '/content/drive/MyDrive/BishopThesisv10-3dLandmark-unity/BlazePose_input_output/3d_output_txt/3d_landmarks_1234.txt'
landmark_keys=[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13,14, 15,16, 17,18, 19,20, 21,22, 23, 24, 25,26, 27,28, 29,30, 31, 32]
save_coordinates(filename,landmarks_3d,landmark_keys)


plot 3d Skeleton

In [ ]:
  # import plotly.graph_objects as go

# # Load the 3D landmarks from the saved file
# # landmarks_3d = np.loadtxt('3d_landmarks.txt')
# landmarks_3d = landmarks_3d
# print(landmarks_3d)

# # Define the skeleton connections
# connections = [
#     [0, 1], [1, 2], [2, 3], [3, 7], [7, 6], [6, 5], [5, 4],
#     [3, 13], [13, 12], [12, 11], [11, 10],
#     [3, 9], [9, 8], [8, 15], [15, 14],
#     [8, 4], [4, 16], [16, 17], [17, 18], [18, 19], [19, 20],
#     [14, 21], [21, 22], [22, 23], [23, 24], [14, 25], [25, 26],
#     [26, 27], [27, 28], [28, 29], [29, 30]
# ]

# # Create an empty 3D plot
# fig = go.Figure()

# # Plot each frame of the animation
# for landmarks in landmarks_3d:
#     # Plot the skeleton connections
#     for connection in connections:
#         start_point = landmarks[connection[0]]
#         end_point = landmarks[connection[1]]
#         fig.add_trace(go.Scatter3d(
#             x=[start_point[0], end_point[0]],
#             y=[start_point[1], end_point[1]],
#             z=[start_point[2], end_point[2]],
#             mode='lines',
#             line=dict(color='blue'),
#             opacity=0.7
#         ))

#     # Add a point for each landmark
#     fig.add_trace(go.Scatter3d(
#         x=landmarks[:,0],
#         y=landmarks[:,1],
#         z=landmarks[:,2],
#         mode='markers',
#         marker=dict(color='red', size=3),
#         opacity=0.7
#     ))

#     # Set the plot limits and labels
#     fig.update_layout(
#         scene=dict(
#             xaxis=dict(range=[-1,1], title='X'),
#             yaxis=dict(range=[-1,1], title='Y'),
#             zaxis=dict(range=[-1,1], title='Z'),
#         )
#     )

#     # Display the plot
#     fig.show()

# # ---I have to change this code to plot for all frames and with go library---the below code is correct
# %matplotlib inline
# import matplotlib.pyplot as plt
# from mpl_toolkits.mplot3d import Axes3D

# # Load the 3D landmarks from the saved file
# # landmarks_3d = np.loadtxt('3d_landmarks.txt')
# landmarks_3d =landmarks_3d
# # print(landmarks_3d)

# # Define the skeleton connections
# connections =[[15, 21], [16, 20], [18, 20], [3, 7], [14, 16], [23, 25], [28, 30], [11, 23], [27, 31], [6, 8], [15, 17], [24, 26], [16, 22], [4, 5], [5, 6], [29, 31], [12, 24], [23, 24], [0, 1], [9, 10], [1, 2], [0, 4], [11, 13], [30, 32], [28, 32], [15, 19], [16, 18], [25, 27], [26, 28], [12, 14], [17, 19], [2, 3], [11, 12], [27, 29], [13, 15]]
# #  [    [0, 1], [1, 2], [2, 3], [3, 7], [7, 6], [6, 5], [5, 4],
# #     [3, 13], [13, 12], [12, 11], [11, 10],
# #     [3, 9], [9, 8], [8, 15], [15, 14],
# #     [8, 4], [4, 16], [16, 17], [17, 18], [18, 19], [19, 20],
# #     [14, 21], [21, 22], [22, 23], [23, 24], [14, 25], [25, 26],
# #     [26, 27], [27, 28], [28, 29], [29, 30]
# # ]

# # Create a 3D plot
# fig = plt.figure()
# ax = fig.add_subplot(111, projection='3d')

# # Plot each frame of the animation
# for landmarks in landmarks_3d:
#     # Plot the skeleton connections
#     for connection in connections:
#         start_point = landmarks[connection[0]]
#         end_point = landmarks[connection[1]]
#         # ax.plot([start_point[0], end_point[0]], [start_point[1], end_point[1]], [start_point[2], end_point[2]], color='blue')
#         ax.plot([-start_point[2], -end_point[2]],[start_point[0], end_point[0]], [-start_point[1], -end_point[1]], color='blue')
    
#     # Add a point for each landmark
#     # ax.scatter(landmarks[:,0], landmarks[:,1], landmarks[:,2], color='red')
#     ax.scatter(-landmarks[:,2], landmarks[:,0],-landmarks[:,1], color='red')

#     # Set the plot limits and labels
#     # ax.set_xlim(-1, 1)
#     # ax.set_ylim(-1, 1)
#     # ax.set_zlim(-1, 1)
#     ax.set_xlim(-0.5, 0.5)
#     ax.set_ylim(-0.5, 0.5)
#     ax.set_zlim(-0.5, 0.5)
#     ax.set_xlabel('X')
#     ax.set_ylabel('Y')
#     ax.set_zlabel('Z')
    
#     # Display the plot
#     plt.show()
# # ------------------------------


landmarks =np.array(landmarks_3d)
print(landmarks)

import plotly.graph_objects as go
import numpy as np

# Extract the number of frames (N) and number of landmarks (M)
N, M, _ = landmarks.shape

# Create an empty figure
fig = go.Figure()

# Iterate over each frame
for i in range(N):
    # Extract the x, y, z coordinates for the current frame
    x = landmarks[i, :, 0]
    y = landmarks[i, :, 1]
    z = landmarks[i, :, 2]

    # Add the scatter plot of the landmarks for the current frame
    fig.add_trace(go.Scatter3d(
        x=x,
        y=y,
        z=z,
        mode='markers',
        marker=dict(
            size=5,
            color='blue',
            opacity=0.8
        ),
        name=f'Frame {i+1}'
    ))

    # Add the lines connecting the landmarks for the current frame
    for connection in connections:
        idx1, idx2 = connection
        fig.add_trace(go.Scatter3d(
            x=[x[idx1], x[idx2]],
            y=[y[idx1], y[idx2]],
            z=[z[idx1], z[idx2]],
            mode='lines',
            line=dict(
                color='red',
                width=2
            ),
            showlegend=False
        ))

# Set the layout and axis labels
fig.update_layout(
    scene=dict(
        xaxis=dict(title='X'),
        yaxis=dict(title='Y'),
        zaxis=dict(title='Z')
    ),
    title='3D Skeleton Visualization'
)

# Show the plot
fig.show()



[[[-1. -1. -1.]
  [-1. -1. -1.]
  [-1. -1. -1.]
  ...
  [-1. -1. -1.]
  [-1. -1. -1.]
  [-1. -1. -1.]]

 [[-1. -1. -1.]
  [-1. -1. -1.]
  [-1. -1. -1.]
  ...
  [-1. -1. -1.]
  [-1. -1. -1.]
  [-1. -1. -1.]]

 [[-1. -1. -1.]
  [-1. -1. -1.]
  [-1. -1. -1.]
  ...
  [-1. -1. -1.]
  [-1. -1. -1.]
  [-1. -1. -1.]]

 ...

 [[-1. -1. -1.]
  [-1. -1. -1.]
  [-1. -1. -1.]
  ...
  [-1. -1. -1.]
  [-1. -1. -1.]
  [-1. -1. -1.]]

 [[-1. -1. -1.]
  [-1. -1. -1.]
  [-1. -1. -1.]
  ...
  [-1. -1. -1.]
  [-1. -1. -1.]
  [-1. -1. -1.]]

 [[-1. -1. -1.]
  [-1. -1. -1.]
  [-1. -1. -1.]
  ...
  [-1. -1. -1.]
  [-1. -1. -1.]
  [-1. -1. -1.]]]
